# Feature Tracking and Optical Flow

In this notebook we explore three techniques to solve the tracking problem:
1. [Feature Tracking](#1-feature-tracking)
2. [Sparse Optical Flow](#2-sparse-optical-flow)
3. [Dense Optical Flow](#3-dense-optical-flow)



## Imports and Colab

In [1]:
import cv2
import numpy as np
import matplotlib.pyplot as plt
import pickle

In [2]:
def plot_image(title, image):
    cv2.imshow(title, image)

    cv2.waitKey(0)
    cv2.destroyAllWindows()

# 1. Feature Tracking
In this first part, we'll start by tracking visual features.

In [3]:
# Load Different Image Pairs
img1 = cv2.imread("data/images/image0.jpg")
img2 = cv2.imread("data/images/image1.jpg")

# Initialize the FAST detector and BRIEF descriptor
fast = cv2.xfeatures2d.StarDetector_create()
brief = cv2.xfeatures2d.BriefDescriptorExtractor_create()

In [4]:
# Detector
kp = fast.detect(img1,None)

# Descriptor
kp1, des1 = brief.compute(img1, kp)

# Draw the keypoints on the image
img1_kp = cv2.drawKeypoints(img1, kp1, None, color=(0,255,0), flags=0)
plot_image("Image 1 Keypoints", img1_kp)

In [5]:
# Detector
kp = fast.detect(img2,None)

# Descriptor
kp2, des2 = brief.compute(img2, kp)

# Draw the keypoints on the image
img2_kp = cv2.drawKeypoints(img2, kp2, None, color=(0,255,0), flags=0)
plot_image("Image 2 Keypoints", img2_kp)

In [6]:
# FLANN matching
FLANN_INDEX_KDTREE = 0
index_params = dict(algorithm = FLANN_INDEX_KDTREE, trees = 5)
search_params = dict(checks = 50)

flann = cv2.FlannBasedMatcher(index_params, search_params)

matches = flann.knnMatch(np.float32(des1),np.float32(des2),k=2) # Use NP.FLOAT32 for ORB, BRIEF, etc

# store all the good matches as per Lowe's ratio test.
good_matches = []
for m,n in matches:
    if m.distance < 0.7*n.distance:
        good_matches.append(m)

if len(good_matches)>10:
    p1 = np.float32([ kp1[m.queryIdx].pt for m in good_matches ]).reshape(-1,1,2)
    p2 = np.float32([ kp2[m.trainIdx].pt for m in good_matches ]).reshape(-1,1,2)

draw_params = dict(matchColor = (0,255,0), # draw matches in green color
                    singlePointColor = None,
                    flags = 2)

img_briefmatch = cv2.drawMatches(img1, kp1, img2, kp2, good_matches, None, **draw_params)
plot_image("BRIEF Match", img_briefmatch)

# 2. Sparse Optical Flow

In this first part of the tutorial, we'll explore Sparse Optical Flow. This technique is about calculating Optical Flow only for specific features, and not for every pixel. It is faster but not very accurate.

The algorithm we'll use for Feature Detection is the **Shi-Tomasi** detector, and the one we'll use for Optical Flow is called **Lucas-Kanade**.

These are the more "traditional" approaches. 

### First, let's calculate the Sparse Optical Flow on two consecutive images

In [7]:
# Load two consecutive images
im1 = cv2.imread("data/images/image0.jpg")
im2 = cv2.imread("data/images/image1.jpg")

plot_image("Image 1", im1)
plot_image("Image 2", im2)

In [8]:
# Create an Empty mask and define the color of output to green
mask = np.zeros_like(im1)
color = (0, 255, 0)

In [9]:
# Convert both images to grayscale
gray1 = cv2.cvtColor(im1, cv2.COLOR_BGR2GRAY)
gray2 = cv2.cvtColor(im2, cv2.COLOR_BGR2GRAY)

plot_image("Grayscale Image 1", gray1)
plot_image("Grayscale Image 2", gray2)

Define the parameters and launch the **Shi-Tomasi corner detector** on the first image. 

According to OpenCV: 
> _"As usual, image should be a **grayscale image**. Then you specify **number of corners you want to find**. Then you specify the **quality level**, which is a value between 0-1, which denotes the **minimum quality of corner below which everyone is rejected**. Then we provide the **minimum euclidean distance between corners detected**."_

Refer to the OpenCV docs to [see more about how to define the parameters](https://docs.opencv.org/master/dd/d1a/group__imgproc__feature.html#ga1d6bb77486c8f92d79c8793ad995d541).

In [10]:
feature_params = dict(maxCorners = 300, qualityLevel = 0.0025, minDistance = 15, blockSize = 2) # Default 300, 0.25, 3, 7
prev = cv2.goodFeaturesToTrack(gray1, mask = None, **feature_params)

In [11]:
print(feature_params)
print(prev[0])

{'maxCorners': 300, 'qualityLevel': 0.0025, 'minDistance': 15, 'blockSize': 2}
[[477.  16.]]


In [12]:
# Go through each detected corner, and draw a dot
image_corners = im1.copy()

for i in prev:
    x,y = i.ravel()
    cv2.circle(image_corners,(int(x),int(y)),3,255,-1)

plot_image("Image Corners", image_corners)

Launch the Lucas Kanade Optical Flow algorithm with the features and both grayscale images.

See the [OpenCV docs for the `calcOpticalFlowPyrLK()` function](https://docs.opencv.org/4.5.3/dc/d6b/group__video__track.html#ga473e4b886d0bcc6b65831eb88ed93323).

In [13]:
lk_params = dict(winSize=(15,15), 
                 maxLevel=2,
                 criteria=(cv2.TERM_CRITERIA_EPS | cv2.TERM_CRITERIA_COUNT, 10, 0.03))

next, status, error = cv2.calcOpticalFlowPyrLK(gray1, gray2, prev, None, **lk_params)

In [14]:
print(lk_params)
idx = 19
print(prev[idx])
print(next[idx])
print(status[idx])
print(error[idx])

{'winSize': (15, 15), 'maxLevel': 2, 'criteria': (3, 10, 0.03)}
[[659.   6.]]
[[666.6108    -9.550047]]
[0]
[6.2071626e-36]


In [15]:
# Store the Matches (status=1 means a match)
good_matches_old = prev[status == 1]
good_matches_new = next[status == 1]

In [16]:
# Go through each matched feature, and draw it on the second image

for new, old in zip(good_matches_new, good_matches_old):
    a, b = new.ravel()
    c, d = old.ravel()
    
    mask = cv2.arrowedLine(mask, (int(a), int(b)), (int(c), int(d)), color, 2)
    im2 = cv2.circle(im2, (int(a), int(b)), 3, color, -1)

# Overlays the optical flow tracks on the original frame
output = cv2.add(im2, mask)

# Updates previous frame
gray1 = gray2.copy()

# Updates previous good feature points
prev = good_matches_new.reshape(-1, 1, 2)

#cv2.imwrite("output.jpg", output)
plot_image("Output", output)

In [17]:
plot_image("Image Mask", mask)

### On a video

In [18]:
def lk_from_image(image):
    global idx, gray1, mask, prev
    if idx==0:
        gray1 = cv2.cvtColor(image, cv2.COLOR_BGR2GRAY)
        feature_params = dict(maxCorners = 600, qualityLevel = 0.0025, minDistance = 15, blockSize = 2)
        prev = cv2.goodFeaturesToTrack(gray1, mask = None, **feature_params)
        mask = np.zeros_like(image)
        idx+=1
        return image
    # Else
    im2 = image
    if idx%15==0:
        mask = np.zeros_like(image)
    
    if idx%5==0:
        # Every 5 images, relaunch the feature detection
        feature_params = dict(maxCorners = 300, qualityLevel = 0.2, minDistance = 2, blockSize = 7)
        prev = cv2.goodFeaturesToTrack(gray1, mask = None, **feature_params)
    
    color = (0, 255, 0)
    gray2 = cv2.cvtColor(im2, cv2.COLOR_BGR2GRAY)
 
    lk_params = dict(winSize = (15,15), maxLevel = 2, criteria = (cv2.TERM_CRITERIA_EPS | cv2.TERM_CRITERIA_COUNT, 10, 0.03))
    next, status, error = cv2.calcOpticalFlowPyrLK(gray1, gray2, prev, None, **lk_params)

    good_matches_old = prev[status == 1]
    good_matches_new = next[status == 1]

    for new, old in zip(good_matches_new, good_matches_old):
        a, b = new.ravel()
        c, d = old.ravel()            
        mask = cv2.arrowedLine(mask, (int(a), int(b)), (int(c), int(d)), color, 2)
        im2 = cv2.circle(im2, (int(a), int(b)), 3, color, -1)

    output = cv2.add(im2, mask)
    gray1 = gray2.copy()
    prev = good_matches_new.reshape(-1, 1, 2)
    idx += 1
    
    return output

In [19]:
from moviepy.editor import VideoFileClip
idx = 0

video_file = "data/videos/skateboard.mp4"
clip = VideoFileClip(video_file).subclip(0,20)
white_clip = clip.fl_image(lk_from_image)
%time white_clip.write_videofile("output/output_lk_skateboard.mp4",audio=False)

Moviepy - Building video output/output_lk_skateboard.mp4.
Moviepy - Writing video output/output_lk_skateboard.mp4



Moviepy - Done !
Moviepy - video ready output/output_lk_skateboard.mp4
CPU times: user 6.66 s, sys: 4.67 s, total: 11.3 s
Wall time: 7.09 s


In [20]:
from IPython.display import HTML
from base64 import b64encode

mp4 = open('output/output_lk_skateboard.mp4','rb').read()
data_url = "data:video/mp4;base64," + b64encode(mp4).decode()
HTML("""
<video width=800 controls>
      <source src="%s" type="video/mp4">
</video>
""" % data_url)

# 3. Dense Optical Flow

In this second part, we'll try to learn about Dense Optical Flow; which is used when **we're tracking every pixel of an image**. It's **longer** but **works much better**.

### Let's do the Dense Optical Flow on two consecutive images

In [21]:
#Load the 2 consecutive images and convert them to grayscale
im1 = cv2.imread("data/images/image0.jpg")
im2 = cv2.imread("data/images/image1.jpg")
gray1 = cv2.cvtColor(im1, cv2.COLOR_BGR2GRAY)
gray2 = cv2.cvtColor(im2, cv2.COLOR_BGR2GRAY)

In [22]:
#Create a mask in HSV Color Space.
hsv = np.zeros_like(im1)
# Sets image saturation to maximum.
hsv[..., 1] = 255

Now comes the Optical Flow Algorithm. This time, we'll use the Farneback algorithm (2003).
Unlike the Lucas Kanade method, we don't want to find "next, status, and error". This time, we just want to estimate one output, the **flow**.

If you'd like to understand how to tweak the parameters, you can [visit this link](https://docs.opencv.org/3.0-beta/modules/video/doc/motion_analysis_and_object_tracking.html#calcopticalflowfarneback).

The next step is to calculate this flow, and convert it into a visual output.

In [23]:
flow = cv2.calcOpticalFlowFarneback(gray1, gray2, None, 0.5, 3, 15, 3, 5, 1.2, 0)

### But what is the Flow?
**The Flow is a 2D Matrix** that has the same size as our input frame (image 1). In this matrix, we have the **optical flow vectors U and V**. These are made of point coordinates. **For any point P (x,y) in the grayscale image, the flow contains the corresponding (delta_x, delta_y)**, i.e., how much did that pixel move in the X and Y direction.

In [24]:
print("Shapes Gray & Flow")
print(gray1.shape)
print(flow.shape)
print(" ")

print("Flow Output")
print(flow)
print(" ")

print("U Vector")
print(flow[...,0])
print(" ")

print("V Vector")
print(flow[...,1])
print(" ")

Shapes Gray & Flow
(432, 768)
(432, 768, 2)
 
Flow Output
[[[-8.606705   -0.46653652]
  [-8.967901   -0.5036245 ]
  [-9.011185   -0.5011998 ]
  ...
  [23.189276   -8.995762  ]
  [23.200577   -9.006791  ]
  [22.84172    -9.010163  ]]

 [[-8.669753   -0.6251331 ]
  [-8.971131   -0.624706  ]
  [-9.027629   -0.61310124]
  ...
  [23.269274   -8.964831  ]
  [23.309032   -8.968984  ]
  [23.059587   -8.960802  ]]

 [[-8.697428   -0.649018  ]
  [-8.95854    -0.64226425]
  [-9.0307255  -0.6300936 ]
  ...
  [23.46124    -8.884274  ]
  [23.560646   -8.883723  ]
  [23.502108   -8.867053  ]]

 ...

 [[ 4.4493804  -6.9319096 ]
  [ 5.515306   -7.9730816 ]
  [ 6.740018   -8.880184  ]
  ...
  [-8.005964   -2.4440458 ]
  [-5.9824815  -1.8417977 ]
  [-4.240536   -1.2768935 ]]

 [[ 4.2441535  -6.651492  ]
  [ 5.438955   -7.7849603 ]
  [ 6.6974072  -8.714903  ]
  ...
  [-7.782724   -2.3513496 ]
  [-5.68055    -1.7401717 ]
  [-3.9246738  -1.1770893 ]]

 [[ 3.5780997  -5.795508  ]
  [ 4.8877645  -7.0012627 ]


**We have 2 vectors U and V**, which correspond to the first and second column of the flow output in cartesian coordinates.

---

According to OpenCV: "We get **a 2-channel array** with **optical flow vectors, (u,v)**. We find their **magnitude** and **direction**. We color code the result for better visualization. **Direction corresponds to Hue** value of the image. **Magnitude corresponds to Value plane**."

---

In other words, it's possible to make something with "the point moved 2 pixels to the right"! We find the Magnitude and Angle, convert that to HSV Space (Hue, Saturation, Value) and then make it an image.

I know this sounds horrible, but we need to go back to High School Maths (or maybe college), and remember about Vectors in Cartesian and Polar coordinates. Of course, **the vectors represent the displacements of each pixels.**

*   A vector in **cartesian** coordinates has its values in **(x,y)**.
*   A vector in **polar** coordinates has its values in **Radian**.
![](https://cdn.kastatic.org/ka-perseus-images/1559d8785a298fdd0bac0443388b3812c4327ec3.png)

To compute the Polar coordinates, we must calculate the magnitude and the angle of the vector.

In [25]:
# Computes the magnitude and angle of the 2D vectors
magnitude, angle = cv2.cartToPolar(flow[..., 0], flow[..., 1])

print(magnitude)
print(angle)

[[ 8.61934    8.982032   9.025113  ... 24.873003  24.887527  24.554577 ]
 [ 8.692262   8.992856   9.048424  ... 24.936466  24.97506   24.739452 ]
 [ 8.721609   8.981533   9.05268   ... 25.087051  25.179846  25.119188 ]
 ...
 [ 8.237012   9.694774  11.148341  ...  8.370712   6.259577   4.428612 ]
 [ 7.8901954  9.496728  10.991123  ...  8.130169   5.941115   4.0973897]
 [ 6.8110733  8.538613  10.181647  ...  6.552034   4.4436617  2.822607 ]]
[[3.1957355 3.1976817 3.1971445 ... 5.9130516 5.912803  5.9073853]
 [3.2135606 3.2111032 3.2093904 ... 5.9153686 5.915786  5.912473 ]
 [3.2160637 3.2131507 3.2112396 ... 5.921117  5.922536  5.922334 ]
 ...
 [5.2829237 5.317422  5.361523  ... 3.4379382 3.4403043 3.4341247]
 [5.2802353 5.3220787 5.367537  ... 3.4350493 3.4389086 3.4330275]
 [5.2654166 5.3217273 5.376289  ... 3.4252064 3.4279673 3.421077 ]]


In [26]:
# Sets image hue according to the optical flow direction
hsv[..., 0] = angle * 180 / np.pi / 2

print(hsv)

[[[ 91 255   0]
  [ 91 255   0]
  [ 91 255   0]
  ...
  [169 255   0]
  [169 255   0]
  [169 255   0]]

 [[ 92 255   0]
  [ 91 255   0]
  [ 91 255   0]
  ...
  [169 255   0]
  [169 255   0]
  [169 255   0]]

 [[ 92 255   0]
  [ 92 255   0]
  [ 91 255   0]
  ...
  [169 255   0]
  [169 255   0]
  [169 255   0]]

 ...

 [[151 255   0]
  [152 255   0]
  [153 255   0]
  ...
  [ 98 255   0]
  [ 98 255   0]
  [ 98 255   0]]

 [[151 255   0]
  [152 255   0]
  [153 255   0]
  ...
  [ 98 255   0]
  [ 98 255   0]
  [ 98 255   0]]

 [[150 255   0]
  [152 255   0]
  [154 255   0]
  ...
  [ 98 255   0]
  [ 98 255   0]
  [ 98 255   0]]]


In [27]:
# Sets image value according to the optical flow magnitude (normalized)
hsv[..., 2] = cv2.normalize(magnitude, None, 0, 255, cv2.NORM_MINMAX)
print(hsv)

[[[ 91 255  55]
  [ 91 255  57]
  [ 91 255  57]
  ...
  [169 255 159]
  [169 255 159]
  [169 255 157]]

 [[ 92 255  55]
  [ 91 255  57]
  [ 91 255  58]
  ...
  [169 255 160]
  [169 255 160]
  [169 255 158]]

 [[ 92 255  55]
  [ 92 255  57]
  [ 91 255  58]
  ...
  [169 255 161]
  [169 255 161]
  [169 255 161]]

 ...

 [[151 255  52]
  [152 255  62]
  [153 255  71]
  ...
  [ 98 255  53]
  [ 98 255  40]
  [ 98 255  28]]

 [[151 255  50]
  [152 255  60]
  [153 255  70]
  ...
  [ 98 255  52]
  [ 98 255  38]
  [ 98 255  26]]

 [[150 255  43]
  [152 255  54]
  [154 255  65]
  ...
  [ 98 255  42]
  [ 98 255  28]
  [ 98 255  18]]]


In [28]:
plot_image("HSV Image", hsv)

In [29]:
# Converts HSV to RGB (BGR) color representation
rgb = cv2.cvtColor(hsv, cv2.COLOR_HSV2RGB)

In [30]:
# Display the Output
cv2.imwrite("output/Dense Output.jpg",rgb)
plot_image("RGB Image", rgb)

![](https://www.researchgate.net/profile/Christophoros-Nikou/publication/266149545/figure/fig1/AS:392088710598656@1470492641144/The-optical-flow-field-color-coding-Smaller-vectors-are-lighter-and-color-represents-the.png)

### On a video

In [31]:
def farneback_from_image(image):
    global idx, im1
    if idx==0:
        im1 = image
        idx+=1
        return im1
    else:
        im2 = image
        gray1 = cv2.cvtColor(im1, cv2.COLOR_BGR2GRAY)
        gray2 = cv2.cvtColor(im2, cv2.COLOR_BGR2GRAY)
        hsv = np.zeros_like(im1)
        hsv[..., 1] = 255
        flow = cv2.calcOpticalFlowFarneback(gray1, gray2, None, 0.5, 3, 15, 3, 5, 1.2, 0)
        magnitude, angle = cv2.cartToPolar(flow[..., 0], flow[..., 1])
        hsv[..., 0] = angle * 180 / np.pi / 2
        hsv[..., 2] = cv2.normalize(magnitude, None, 0, 255, cv2.NORM_MINMAX)
        bgr = cv2.cvtColor(hsv, cv2.COLOR_HSV2RGB)
        idx+=1
        im1= image.copy()
        return bgr

In [32]:
from moviepy.editor import VideoFileClip
idx = 0

video_file = "data/videos/skateboard.mp4"
clip = VideoFileClip(video_file).subclip(0,10)
white_clip = clip.fl_image(farneback_from_image)
%time white_clip.write_videofile("output/output_farneback.mp4",audio=False)

Moviepy - Building video output/output_farneback.mp4.
Moviepy - Writing video output/output_farneback.mp4



Moviepy - Done !
Moviepy - video ready output/output_farneback.mp4
CPU times: user 50.2 s, sys: 5.94 s, total: 56.2 s
Wall time: 53.1 s


In [33]:
from IPython.display import HTML
from base64 import b64encode
mp4 = open('output/output_farneback.mp4','rb').read()
data_url = "data:video/mp4;base64," + b64encode(mp4).decode()
HTML("""
<video width=800 controls>
      <source src="%s" type="video/mp4">
</video>
""" % data_url)